# SQLite3 browser
2025-04-13 create

In [1]:
import os
import glob
import pandas as pd
import ipywidgets as widgets
import usqlite3

In [2]:
pd.set_option('display.max_rows', 1000)

initdirname = os.getcwd()

output_debug = widgets.Output()

## タブ1（構造）

In [3]:
def show_table_info(tablename):
    output_info.clear_output()
    if not tablename:
        return
    df = db.get_table_info(tablename)
    df = df.set_index("cid")
    with output_info:
        display(df)

output_info = widgets.Output()

tab1 = widgets.VBox([
    output_info
])

## タブ2（データ）

In [8]:
output_data = widgets.Output()

label_n_row = widgets.HTML()

button_back = widgets.Button(
    description="<",
    layout=widgets.Layout(width="30px"))

button_forward = widgets.Button(
    description=">",
    layout=widgets.Layout(width="30px"))

text_pages = widgets.BoundedIntText(
    min=1,
    layout={"width": "fit-content"})

label_n_page = widgets.Label("")

dropdown_rowwidth = widgets.Dropdown(
    value=25,
    options=[10, 25, 50, 100],
    description="Rows/page",
    layout=widgets.Layout(width="10rem"))

n_page = 0

def move_to_prev_page(b):
    page = text_pages.value
    page = max(1, page - 1)
    text_pages.value = page
button_back.on_click(move_to_prev_page)

def move_to_next_page(b):
    page = text_pages.value
    page = min(n_page, page + 1)
    text_pages.value = page
button_forward.on_click(move_to_next_page)

def update_table(page):
    output_data.clear_output()

    tablename = dropdown_table.value
    rowwidth = dropdown_rowwidth.value

    if not tablename:
        return

    offset = rowwidth * (page - 1)
    limit = rowwidth
    
    sql = f'SELECT * FROM "{tablename}" LIMIT {limit} OFFSET {offset}'
    df = pd.read_sql_query(sql, db.con)

    # シフトさせる
    df.index = df.index + offset + 1

    # 表示
    with output_data:
        display(df)

def page_changed(change):
    page = change.new
    update_table(page)
text_pages.observe(page_changed, names="value")

def rowwidth_changed(change):
    tablename = dropdown_table.value
    reset_data_tab(tablename)
dropdown_rowwidth.observe(rowwidth_changed, names="value")

def reset_data_tab(tablename):
    global n_page
    rowwidth = dropdown_rowwidth.value

    if not tablename:
        label_n_row.value = ""
        n_page = 1
        text_pages.value = 1
        label_n_page.value = "-"
        text_pages.max = n_page
        update_table(1)
        return

    n_row = db.count(tablename)
    if n_row == 0:
        n_page = 1
        text_pages.value = 1
        label_n_page.value = "-"
    else:
        n_page = (n_row - 1) // rowwidth + 1
        text_pages.value = 1
        label_n_page.value = f"(1 - {n_page})"
    text_pages.value = 1
    text_pages.max = n_page

    # 行数ラベルの更新
    label_n_row.value = f"<b>{n_row:,}</b>"

    # テーブルの更新
    update_table(1)

tab2 = widgets.VBox([
    widgets.HBox([widgets.Label(value="Number of rows:"), label_n_row]),
    widgets.HBox([button_back, text_pages, button_forward, label_n_page, dropdown_rowwidth]),
    output_data
])

## データベースとテーブル

In [9]:
label_dbname = widgets.HTML()

dropdown_table = widgets.Dropdown(
    options=[],
    layout={"width": "max-content"})

def table_changed(change):
    update_tab_contents()
dropdown_table.observe(table_changed, names="value")

def update_tab_contents():
    tablename = dropdown_table.value
    show_table_info(tablename)
    reset_data_tab(tablename)

db = None
def set_dbfilename(filename):
    global db
    dropdown_table.options = []

    if not filename:
        db = None
        label_dbname.value = "(None)"
        return

    db = usqlite3.open(filename)
    label_dbname.value = f"<b>{db.filename}</b>"

    # テーブル更新
    tables = db.get_table_names()
    dropdown_table.options = tables

widgets_db_table = widgets.VBox([
    widgets.HBox([widgets.Label(value="DB filename:"), label_dbname]),
    widgets.HBox([widgets.Label(value="Tablename:"), dropdown_table])
])

## ファイル選択

In [10]:
buttons_path = widgets.HBox(layout={"width": "fit-content"})
dropdown_filename = widgets.Dropdown(
    layout={"width": "max-content"})
button_load = widgets.Button(
    description="Load",
    layout={"width": "fit-content"})

def path_button_clicked(b):
    dirname = b.tooltip
    update_path_row(dirname)

def path_dropdown_selected(change):
    dirname = change.new
    update_path_row(dirname)

def update_path_row(dirname):
    # 相対パスのときでも絶対パスにする
    dirname = os.path.abspath(dirname)
    
    # DBファイル一覧
    ls_dbfile = glob.glob(os.path.join(dirname, "*.sqlite3"))
    ls_dbfile.sort()
    dropdown_filename.options = [(os.path.basename(x), x) for x in ls_dbfile]

    # ディレクトリ一覧
    ls_dir = [x for x in os.listdir(dirname) if \
        os.path.isdir(os.path.join(dirname, x)) and \
        (not x.startswith(".")) and \
        (x != "__pycache__")
    ]
    ls_dir.sort()
    dropdown_dir = widgets.Dropdown(layout={"width": "max-content"})
    dropdown_dir.options = [(x, os.path.join(dirname, x)) for x in ls_dir]
    dropdown_dir.observe(path_dropdown_selected, names="value")

    # パスを分解
    ls_name = []
    for i in range(50):
        dirdirname = os.path.dirname(dirname)
        if dirname == dirdirname:
            # これ以上遡れない
            ls_name = [dirname] + ls_name
            break
        basename = os.path.basename(dirname)
        ls_name = [basename] + ls_name
        dirname = dirdirname

    # ボタン作成
    ls_button = []
    for i in range(len(ls_name)):
        w = widgets.Button(
            description=ls_name[i],
            tooltip=os.path.join(*ls_name[:i+1]),
            layout={"width": "fit-content"}
        )
        w.on_click(path_button_clicked)
        ls_button.append(w)

    # ボタン配置更新
    buttons_path.children = ls_button + [dropdown_dir]

update_path_row(initdirname)

def get_selected_filename():
    return dropdown_filename.value

widgets_path = widgets.VBox([
        buttons_path,
        widgets.HBox([widgets.Label(value="Filename"), dropdown_filename, button_load])
])

## ウィジェット表示

In [11]:
display(widgets_path)
display(widgets.HTML(value="<hr>"))
display(widgets_db_table)

tab = widgets.Tab(
    children=[tab1, tab2],
    titles=["Structure", "Data"]
)
display(tab)

output_debug.clear_output()
display(output_debug)

def update_dbfile(b):
    dbfilename = get_selected_filename()
    set_dbfilename(dbfilename)
    update_tab_contents()

# 初期化
set_dbfilename(None)

button_load.on_click(update_dbfile)

HTML(value='<hr>')

Output()

----